In [1]:
!pip install torch torchvision tqdm
import torch, os
import torchvision
import torchvision.transforms as transforms
from tqdm import tqdm
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

    100% |████████████████████████████████| 519.5MB 30kB/s 
tcmalloc: large alloc 1073750016 bytes == 0x59564000 @  0x7f4f3bf251c4 0x46d6a4 0x5fcbcc 0x4c494d 0x54f3c4 0x553aaf 0x54e4c8 0x54f4f6 0x553aaf 0x54efc1 0x54f24d 0x553aaf 0x54efc1 0x54f24d 0x553aaf 0x54efc1 0x54f24d 0x551ee0 0x54e4c8 0x54f4f6 0x553aaf 0x54efc1 0x54f24d 0x551ee0 0x54efc1 0x54f24d 0x551ee0 0x54e4c8 0x54f4f6 0x553aaf 0x54e4c8
    100% |████████████████████████████████| 61kB 1.7MB/s 
    100% |████████████████████████████████| 51kB 13.4MB/s 
    100% |████████████████████████████████| 2.0MB 2.6MB/s 
  Found existing installation: Pillow 4.0.0
    Uninstalling Pillow-4.0.0:
      Successfully uninstalled Pillow-4.0.0


In [2]:
transform = transforms.Compose([transforms.ToTensor(),])

trainset = torchvision.datasets.CIFAR10(root='./data', train=True,
                                        download=True, transform=transform)
trainloader = torch.utils.data.DataLoader(trainset, batch_size=4,
                                          shuffle=True, num_workers=2)

testset = torchvision.datasets.CIFAR10(root='./data', train=False,
                                       download=True, transform=transform)
testloader = torch.utils.data.DataLoader(testset, batch_size=4,
                                         shuffle=False, num_workers=2)

classes = ('plane', 'car', 'bird', 'cat',
           'deer', 'dog', 'frog', 'horse', 'ship', 'truck')

Files already downloaded and verified


In [0]:
def train(epoch, trainloader, optimizer, criterion):
    running_loss = 0.0
    for i, data in enumerate(tqdm(trainloader), 0):
        # get the inputs
        inputs, labels = data
        if torch.cuda.is_available():
            inputs, labels = inputs.cuda(), labels.cuda()

        # zero the parameter gradients
        optimizer.zero_grad()

        # forward + backward + optimize
        outputs = net(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()

        # print statistics
        running_loss += loss.item()

    print('epoch %d training loss: %.3f' %
            (epoch + 1, running_loss / (len(trainloader))))

In [0]:
def test(testloader, model):
    correct = 0
    total = 0
    with torch.no_grad():
        for data in tqdm(testloader):
            images, labels = data
            if torch.cuda.is_available():
                images, labels = images.cuda(), labels.cuda()        
            outputs = net(images)
            _, predicted = torch.max(outputs.data, 1)
            total += labels.size(0)
            correct += (predicted == labels).sum().item()

    print('Accuracy of the network on the 10000 test images: %d %%' % (
                                    100 * correct / total))

In [0]:
def classwise_test(testloader, model):
########################################################################
# class-wise accuracy

    class_correct = list(0. for i in range(10))
    class_total = list(0. for i in range(10))
    with torch.no_grad():
        for data in tqdm(testloader):
            images, labels = data
            if torch.cuda.is_available():
                images, labels = images.cuda(), labels.cuda()        
            outputs = net(images)
            _, predicted = torch.max(outputs, 1)
            c = (predicted == labels).squeeze()
            for i in range(4):
                label = labels[i]
                class_correct[label] += c[i].item()
                class_total[label] += 1

    for i in range(10):
        print('Accuracy of %5s : %2d %%' % (
            classes[i], 100 * class_correct[i] / class_total[i]))


In [6]:
num_epochs = 5
learning_rate = 0.001
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        
        self.conv1 = nn.Conv2d(in_channels=3, out_channels=128, kernel_size=5)#32-5+1=28
        self.pool1 = nn.MaxPool2d(kernel_size=2, stride=2)#14
        self.conv2 = nn.Conv2d(in_channels=128, out_channels=256, kernel_size=3)#14-3+1=12
        self.pool2 = nn.MaxPool2d(kernel_size=2, stride=2)#6
        self.conv3 = nn.Conv2d(in_channels=256, out_channels=512, kernel_size=3)#6-3+1=4
        self.pool3 = nn.MaxPool2d(kernel_size=2, stride=2)#2
        self.conv4 = nn.Conv2d(in_channels=512, out_channels=1024, kernel_size=1)#2
        self.pool4= nn.MaxPool2d(kernel_size=2, stride=2)#1
        self.conv5 = nn.Conv2d(in_channels=1024, out_channels=1024, kernel_size=1)#2
        self.fc1 = nn.Linear(in_features=1024*1*1, out_features=512)
        self.fc2 = nn.Linear(in_features=512, out_features=256)
        self.fc3 = nn.Linear(in_features=256, out_features=10)


    def forward(self, x):
        x = self.pool1(F.relu(self.conv1(x)))
        x = self.pool2(F.relu(self.conv2(x)))
        x = self.pool3(F.relu(self.conv3(x)))
        x = self.pool4(F.relu(self.conv4(x)))
        x = F.relu(self.conv5(x))
        
        x = x.view(-1, 1024*1*1)
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x
net = Net()
# transfer the model to GPU
if torch.cuda.is_available():
    net = net.cuda()
    print("Using GPU")

criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=learning_rate, momentum=0.9)

print('Start Training')
os.makedirs('./models', exist_ok=True)

for epoch in range(num_epochs):  # loop over the dataset multiple times
    print('epoch ', epoch + 1)
    train(epoch, trainloader, optimizer, criterion)
    test(testloader, net)
    classwise_test(testloader, net)
    torch.save(net.state_dict(), './models/model-'+str(epoch)+'.pth')

print('Finished Training')

  0%|          | 0/12500 [00:00<?, ?it/s]

Using GPU
Start Training
epoch  1


  0%|          | 0/2500 [00:00<?, ?it/s]

epoch 1 training loss: 2.207


  0%|          | 0/2500 [00:00<?, ?it/s]

...

epoch 5 training loss: 1.002


  0%|          | 0/2500 [00:00<?, ?it/s]

Accuracy of the network on the 10000 test images: 64 %


100%|██████████| 2500/2500 [00:14<00:00, 173.92it/s]

Accuracy of plane : 54 %
Accuracy of   car : 66 %
Accuracy of  bird : 53 %
Accuracy of   cat : 46 %
Accuracy of  deer : 55 %
Accuracy of   dog : 44 %
Accuracy of  frog : 84 %
Accuracy of horse : 76 %
Accuracy of  ship : 72 %
Accuracy of truck : 85 %
Finished Training


In [7]:
print('Epoch 6 to 10')
for epoch in range(5,10):  # loop over the dataset multiple times
    print('epoch ', epoch + 1)
    train(epoch, trainloader, optimizer, criterion)
    test(testloader, net)
    classwise_test(testloader, net)
    torch.save(net.state_dict(), './models/model-'+str(epoch)+'.pth')

print('Finished Training')

  0%|          | 0/12500 [00:00<?, ?it/s]

Epoch 6 to 10
epoch  6


  0%|          | 0/2500 [00:00<?, ?it/s]

epoch 6 training loss: 0.837


  0%|          | 0/2500 [00:00<?, ?it/s]

...

epoch 10 training loss: 0.379


  0%|          | 0/2500 [00:00<?, ?it/s]

Accuracy of the network on the 10000 test images: 73 %


100%|██████████| 2500/2500 [00:13<00:00, 179.13it/s]


Accuracy of plane : 72 %
Accuracy of   car : 89 %
Accuracy of  bird : 59 %
Accuracy of   cat : 59 %
Accuracy of  deer : 69 %
Accuracy of   dog : 58 %
Accuracy of  frog : 83 %
Accuracy of horse : 81 %
Accuracy of  ship : 83 %
Accuracy of truck : 82 %
Finished Training


In [8]:
print('Epoch 11 to 15')
for epoch in range(10,15):  # loop over the dataset multiple times
    print('epoch ', epoch + 1)
    train(epoch, trainloader, optimizer, criterion)
    test(testloader, net)
    classwise_test(testloader, net)
    torch.save(net.state_dict(), './models/model-'+str(epoch)+'.pth')

print('Finished Training')

  0%|          | 0/12500 [00:00<?, ?it/s]

Epoch 11 to 15
epoch  11


  0%|          | 0/2500 [00:00<?, ?it/s]

epoch 11 training loss: 0.308


  0%|          | 0/2500 [00:00<?, ?it/s]

...

epoch 15 training loss: 0.143


  0%|          | 0/2500 [00:00<?, ?it/s]

Accuracy of the network on the 10000 test images: 70 %


100%|██████████| 2500/2500 [00:13<00:00, 178.66it/s]


Accuracy of plane : 69 %
Accuracy of   car : 71 %
Accuracy of  bird : 55 %
Accuracy of   cat : 79 %
Accuracy of  deer : 66 %
Accuracy of   dog : 36 %
Accuracy of  frog : 76 %
Accuracy of horse : 80 %
Accuracy of  ship : 86 %
Accuracy of truck : 87 %
Finished Training


In [13]:
num_epochs = 5
learning_rate = 0.001
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        
        self.conv1 = nn.Conv2d(in_channels=3, out_channels=128, kernel_size=5)#32-5+1=28
        self.pool1 = nn.MaxPool2d(kernel_size=2, stride=2)#14
        self.conv2 = nn.Conv2d(in_channels=128, out_channels=256, kernel_size=3)#14-3+1=12
        self.pool2 = nn.MaxPool2d(kernel_size=2, stride=2)#6
        self.conv3 = nn.Conv2d(in_channels=256, out_channels=512, kernel_size=3)#6-3+1=4
        self.pool3 = nn.MaxPool2d(kernel_size=2, stride=2)#2
        self.conv4 = nn.Conv2d(in_channels=512, out_channels=1024, kernel_size=1)#2
        self.pool4= nn.MaxPool2d(kernel_size=2, stride=2)#1
        #self.conv5 = nn.Conv2d(in_channels=1024, out_channels=1024, kernel_size=1)#2
        self.fc1 = nn.Linear(in_features=1024*1*1, out_features=1024)
        #self.fc2 = nn.Linear(in_features=1024, out_features=10)
        self.fc3 = nn.Linear(in_features=1024, out_features=10)


    def forward(self, x):
        x = self.pool1(F.relu(self.conv1(x)))
        x = self.pool2(F.relu(self.conv2(x)))
        x = self.pool3(F.relu(self.conv3(x)))
        x = self.pool4(F.relu(self.conv4(x)))
        #x = F.relu(self.conv5(x))
        
        x = x.view(-1, 1024*1*1)
        x = F.relu(self.fc1(x))
        #x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x
net = Net()
# transfer the model to GPU
if torch.cuda.is_available():
    net = net.cuda()
    print("Using GPU")

criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=learning_rate, momentum=0.9, weight_decay=0.0001)

print('Start Training')
os.makedirs('./models', exist_ok=True)

for epoch in range(num_epochs):  # loop over the dataset multiple times
    print('epoch ', epoch + 1)
    train(epoch, trainloader, optimizer, criterion)
    test(testloader, net)
    classwise_test(testloader, net)
    torch.save(net.state_dict(), './models/model-'+str(epoch)+'.pth')

print('Finished Training')




  0%|          | 0/12500 [00:00<?, ?it/s]

Using GPU
Start Training
epoch  1





  0%|          | 5/12500 [00:00<04:38, 44.93it/s]


  0%|          | 14/12500 [00:00<03:08, 66.15it/s]


  0%|          | 24/12500 [00:00<02:46, 74.85it/s]


  0%|          | 34/12500 [00:00<02:36, 79.83it/s]


  0%|          | 44/12500 [00:00<02:30, 82.80it/s]


  0%|          | 54/12500 [00:00<02:25, 85.33it/s]


  1%|          | 64/12500 [00:00<02:22, 87.23it/s]


  1%|          | 75/12500 [00:00<02:19, 88.82it/s]


  1%|          | 85/12500 [00:00<02:18, 89.86it/s]


  1%|          | 95/12500 [00:01<02:16, 90.73it/s]


  1%|          | 105/12500 [00:01<02:15, 91.48it/s]


  1%|          | 115/12500 [00:01<02:14, 92.03it/s]


  1%|          | 126/12500 [00:01<02:13, 92.79it/s]


  1%|          | 136/12500 [00:01<02:12, 93.17it/s]


  1%|          | 147/12500 [00:01<02:11, 93.83it/s]


  1%|▏         | 157/12500 [00:01<02:11, 94.06it/s]


  1%|▏         | 167/12500 [00:01<02:11, 94.13it/s]


  1%|▏         | 177/12500 [00:01<02:10, 94.41it/s]


  1%|▏         | 187/12500 [00:01<02

epoch 1 training loss: 1.917





  0%|          | 1/2500 [00:00<04:27,  9.33it/s]


  1%|          | 21/2500 [00:00<00:24, 100.36it/s]


  2%|▏         | 41/2500 [00:00<00:18, 132.15it/s]


  2%|▏         | 61/2500 [00:00<00:16, 148.50it/s]


  3%|▎         | 79/2500 [00:00<00:15, 153.22it/s]


  4%|▍         | 99/2500 [00:00<00:14, 160.56it/s]


  5%|▍         | 120/2500 [00:00<00:14, 166.32it/s]


  6%|▌         | 140/2500 [00:00<00:13, 170.31it/s]


  6%|▋         | 161/2500 [00:00<00:13, 174.17it/s]


  7%|▋         | 182/2500 [00:01<00:13, 177.60it/s]


  8%|▊         | 204/2500 [00:01<00:12, 180.84it/s]


  9%|▉         | 224/2500 [00:01<00:12, 182.26it/s]


 10%|▉         | 246/2500 [00:01<00:12, 184.55it/s]


 11%|█         | 267/2500 [00:01<00:11, 186.25it/s]


 12%|█▏        | 288/2500 [00:01<00:11, 187.17it/s]


 12%|█▏        | 309/2500 [00:01<00:11, 188.24it/s]


 13%|█▎        | 330/2500 [00:01<00:11, 187.73it/s]


 14%|█▍        | 350/2500 [00:01<00:11, 188.35it/s]


 15%|█▍        | 371/2500 [00:01<

...

epoch 5 training loss: 0.791





  0%|          | 6/2500 [00:00<00:44, 56.67it/s]


  1%|          | 27/2500 [00:00<00:18, 130.16it/s]


  2%|▏         | 49/2500 [00:00<00:15, 157.59it/s]


  3%|▎         | 70/2500 [00:00<00:14, 170.10it/s]


  4%|▎         | 92/2500 [00:00<00:13, 179.46it/s]


  4%|▍         | 110/2500 [00:00<00:13, 179.14it/s]


  5%|▌         | 131/2500 [00:00<00:12, 183.12it/s]


  6%|▌         | 152/2500 [00:00<00:12, 186.03it/s]


  7%|▋         | 173/2500 [00:00<00:12, 187.96it/s]


  8%|▊         | 194/2500 [00:01<00:12, 189.57it/s]


  9%|▊         | 215/2500 [00:01<00:11, 191.24it/s]


  9%|▉         | 236/2500 [00:01<00:11, 192.31it/s]


 10%|█         | 257/2500 [00:01<00:11, 193.59it/s]


 11%|█         | 279/2500 [00:01<00:11, 194.81it/s]


 12%|█▏        | 300/2500 [00:01<00:11, 195.73it/s]


 13%|█▎        | 321/2500 [00:01<00:11, 196.04it/s]


 14%|█▎        | 342/2500 [00:01<00:10, 196.58it/s]


 15%|█▍        | 363/2500 [00:01<00:10, 195.45it/s]


 15%|█▌        | 384/2500 [00:01

Accuracy of the network on the 10000 test images: 70 %





  0%|          | 1/2500 [00:00<04:42,  8.86it/s]


  1%|          | 18/2500 [00:00<00:29, 84.39it/s]


  1%|▏         | 35/2500 [00:00<00:22, 109.95it/s]


  2%|▏         | 53/2500 [00:00<00:19, 125.68it/s]


  3%|▎         | 71/2500 [00:00<00:17, 135.45it/s]


  4%|▎         | 89/2500 [00:00<00:16, 142.48it/s]


  4%|▍         | 107/2500 [00:00<00:16, 147.43it/s]


  5%|▌         | 125/2500 [00:00<00:15, 150.46it/s]


  6%|▌         | 143/2500 [00:00<00:15, 153.11it/s]


  6%|▋         | 161/2500 [00:01<00:15, 155.55it/s]


  7%|▋         | 179/2500 [00:01<00:14, 157.33it/s]


  8%|▊         | 197/2500 [00:01<00:14, 158.65it/s]


  9%|▊         | 215/2500 [00:01<00:14, 159.97it/s]


  9%|▉         | 233/2500 [00:01<00:14, 161.04it/s]


 10%|█         | 251/2500 [00:01<00:13, 161.40it/s]


 11%|█         | 269/2500 [00:01<00:13, 161.50it/s]


 11%|█▏        | 287/2500 [00:01<00:13, 162.56it/s]


 12%|█▏        | 305/2500 [00:01<00:13, 163.00it/s]


 13%|█▎        | 324/2500 [00:01<0

Accuracy of plane : 77 %
Accuracy of   car : 80 %
Accuracy of  bird : 74 %
Accuracy of   cat : 55 %
Accuracy of  deer : 58 %
Accuracy of   dog : 41 %
Accuracy of  frog : 79 %
Accuracy of horse : 80 %
Accuracy of  ship : 76 %
Accuracy of truck : 82 %
Finished Training


In [14]:
print('Epoch 6 to 10')
for epoch in range(5,10):  # loop over the dataset multiple times
    print('epoch ', epoch + 1)
    train(epoch, trainloader, optimizer, criterion)
    test(testloader, net)
    classwise_test(testloader, net)
    torch.save(net.state_dict(), './models/model-'+str(epoch)+'.pth')

print('Finished Training')




  0%|          | 0/12500 [00:00<?, ?it/s]

Epoch 6 to 10
epoch  6





  0%|          | 4/12500 [00:00<05:44, 36.25it/s]


  0%|          | 13/12500 [00:00<03:21, 61.93it/s]


  0%|          | 23/12500 [00:00<02:53, 71.92it/s]


  0%|          | 33/12500 [00:00<02:40, 77.69it/s]


  0%|          | 43/12500 [00:00<02:33, 81.06it/s]


  0%|          | 53/12500 [00:00<02:28, 83.71it/s]


  1%|          | 63/12500 [00:00<02:25, 85.30it/s]


  1%|          | 73/12500 [00:00<02:23, 86.68it/s]


  1%|          | 83/12500 [00:00<02:21, 87.77it/s]


  1%|          | 93/12500 [00:01<02:20, 88.40it/s]


  1%|          | 103/12500 [00:01<02:18, 89.25it/s]


  1%|          | 114/12500 [00:01<02:17, 90.36it/s]


  1%|          | 125/12500 [00:01<02:15, 91.23it/s]


  1%|          | 135/12500 [00:01<02:14, 91.65it/s]


  1%|          | 145/12500 [00:01<02:14, 91.80it/s]


  1%|          | 155/12500 [00:01<02:14, 92.06it/s]


  1%|▏         | 165/12500 [00:01<02:13, 92.39it/s]


  1%|▏         | 175/12500 [00:01<02:12, 92.68it/s]


  1%|▏         | 185/12500 [00:01<02

epoch 6 training loss: 0.662





  0%|          | 2/2500 [00:00<02:09, 19.35it/s]


  1%|          | 23/2500 [00:00<00:22, 112.29it/s]


  2%|▏         | 45/2500 [00:00<00:16, 146.26it/s]


  3%|▎         | 67/2500 [00:00<00:14, 163.55it/s]


  4%|▎         | 88/2500 [00:00<00:13, 172.46it/s]


  4%|▍         | 111/2500 [00:00<00:13, 180.44it/s]


  5%|▌         | 133/2500 [00:00<00:12, 185.42it/s]


  6%|▌         | 153/2500 [00:00<00:12, 186.76it/s]


  7%|▋         | 174/2500 [00:00<00:12, 189.30it/s]


  8%|▊         | 195/2500 [00:01<00:12, 190.36it/s]


  9%|▊         | 216/2500 [00:01<00:11, 192.23it/s]


 10%|▉         | 238/2500 [00:01<00:11, 194.30it/s]


 10%|█         | 260/2500 [00:01<00:11, 195.54it/s]


 11%|█         | 281/2500 [00:01<00:11, 195.94it/s]


 12%|█▏        | 302/2500 [00:01<00:11, 196.78it/s]


 13%|█▎        | 324/2500 [00:01<00:10, 198.04it/s]


 14%|█▍        | 346/2500 [00:01<00:10, 199.21it/s]


 15%|█▍        | 368/2500 [00:01<00:10, 200.11it/s]


 16%|█▌        | 390/2500 [00:01

...

epoch 10 training loss: 0.278





  0%|          | 1/2500 [00:00<04:33,  9.12it/s]


  1%|          | 21/2500 [00:00<00:24, 100.61it/s]


  2%|▏         | 43/2500 [00:00<00:17, 138.87it/s]


  3%|▎         | 64/2500 [00:00<00:15, 155.29it/s]


  3%|▎         | 83/2500 [00:00<00:14, 161.74it/s]


  4%|▍         | 105/2500 [00:00<00:14, 170.15it/s]


  5%|▌         | 126/2500 [00:00<00:13, 175.36it/s]


  6%|▌         | 147/2500 [00:00<00:13, 179.23it/s]


  7%|▋         | 168/2500 [00:00<00:12, 182.59it/s]


  8%|▊         | 189/2500 [00:01<00:12, 184.68it/s]


  8%|▊         | 211/2500 [00:01<00:12, 187.45it/s]


  9%|▉         | 233/2500 [00:01<00:11, 189.70it/s]


 10%|█         | 255/2500 [00:01<00:11, 191.38it/s]


 11%|█         | 276/2500 [00:01<00:11, 192.48it/s]


 12%|█▏        | 298/2500 [00:01<00:11, 193.82it/s]


 13%|█▎        | 320/2500 [00:01<00:11, 195.08it/s]


 14%|█▎        | 342/2500 [00:01<00:11, 194.40it/s]


 15%|█▍        | 364/2500 [00:01<00:10, 195.48it/s]


 15%|█▌        | 385/2500 [00:01

Accuracy of the network on the 10000 test images: 73 %





  0%|          | 1/2500 [00:00<04:38,  8.98it/s]


  1%|          | 18/2500 [00:00<00:29, 85.39it/s]


  1%|▏         | 36/2500 [00:00<00:21, 114.33it/s]


  2%|▏         | 52/2500 [00:00<00:19, 124.45it/s]


  3%|▎         | 70/2500 [00:00<00:17, 135.16it/s]


  4%|▎         | 88/2500 [00:00<00:17, 141.71it/s]


  4%|▍         | 106/2500 [00:00<00:16, 146.25it/s]


  5%|▍         | 124/2500 [00:00<00:15, 150.09it/s]


  6%|▌         | 142/2500 [00:00<00:15, 153.06it/s]


  6%|▋         | 160/2500 [00:01<00:15, 155.37it/s]


  7%|▋         | 179/2500 [00:01<00:14, 157.62it/s]


  8%|▊         | 197/2500 [00:01<00:14, 159.28it/s]


  9%|▊         | 215/2500 [00:01<00:14, 160.44it/s]


  9%|▉         | 233/2500 [00:01<00:14, 161.61it/s]


 10%|█         | 251/2500 [00:01<00:13, 162.70it/s]


 11%|█         | 269/2500 [00:01<00:13, 162.09it/s]


 11%|█▏        | 287/2500 [00:01<00:13, 162.86it/s]


 12%|█▏        | 305/2500 [00:01<00:13, 163.69it/s]


 13%|█▎        | 323/2500 [00:01<0

Accuracy of plane : 75 %
Accuracy of   car : 82 %
Accuracy of  bird : 63 %
Accuracy of   cat : 49 %
Accuracy of  deer : 81 %
Accuracy of   dog : 69 %
Accuracy of  frog : 85 %
Accuracy of horse : 67 %
Accuracy of  ship : 85 %
Accuracy of truck : 76 %
Finished Training


In [15]:
num_epochs = 5
learning_rate = 0.001
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        
        self.conv1 = nn.Conv2d(in_channels=3, out_channels=128, kernel_size=5)#32-5+1=28
        self.pool1 = nn.MaxPool2d(kernel_size=2, stride=2)#14
        self.conv2 = nn.Conv2d(in_channels=128, out_channels=256, kernel_size=3)#14-3+1=12
        self.pool2 = nn.MaxPool2d(kernel_size=2, stride=2)#6
        self.conv3 = nn.Conv2d(in_channels=256, out_channels=512, kernel_size=3)#6-3+1=4
        self.pool3 = nn.MaxPool2d(kernel_size=2, stride=2)#2
        self.conv4 = nn.Conv2d(in_channels=512, out_channels=1024, kernel_size=1)#2
        self.pool4= nn.MaxPool2d(kernel_size=2, stride=2)#1
        #self.conv5 = nn.Conv2d(in_channels=1024, out_channels=1024, kernel_size=1)#2
        self.fc1 = nn.Linear(in_features=1024*1*1, out_features=1024)
        #self.fc2 = nn.Linear(in_features=1024, out_features=10)
        self.fc3 = nn.Linear(in_features=1024, out_features=10)


    def forward(self, x):
        x = self.pool1(F.relu(self.conv1(x)))
        x = self.pool2(F.relu(self.conv2(x)))
        x = self.pool3(F.relu(self.conv3(x)))
        x = self.pool4(F.relu(self.conv4(x)))
        #x = F.relu(self.conv5(x))
        
        x = x.view(-1, 1024*1*1)
        x = F.relu(self.fc1(x))
        #x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x
net = Net()
# transfer the model to GPU
if torch.cuda.is_available():
    net = net.cuda()
    print("Using GPU")

criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=learning_rate, momentum=0.9, weight_decay=0.001)

print('Start Training')
os.makedirs('./models', exist_ok=True)

for epoch in range(num_epochs):  # loop over the dataset multiple times
    print('epoch ', epoch + 1)
    train(epoch, trainloader, optimizer, criterion)
    test(testloader, net)
    classwise_test(testloader, net)
    torch.save(net.state_dict(), './models/model-'+str(epoch)+'.pth')

print('Finished Training')




  0%|          | 0/12500 [00:00<?, ?it/s]

Using GPU
Start Training
epoch  1





  0%|          | 3/12500 [00:00<07:26, 28.02it/s]


  0%|          | 11/12500 [00:00<03:55, 53.02it/s]


  0%|          | 20/12500 [00:00<03:16, 63.45it/s]


  0%|          | 29/12500 [00:00<03:00, 69.18it/s]


  0%|          | 38/12500 [00:00<02:52, 72.38it/s]


  0%|          | 47/12500 [00:00<02:47, 74.33it/s]


  0%|          | 56/12500 [00:00<02:44, 75.79it/s]


  1%|          | 64/12500 [00:00<02:44, 75.51it/s]


  1%|          | 73/12500 [00:00<02:42, 76.51it/s]


  1%|          | 82/12500 [00:01<02:40, 77.42it/s]


  1%|          | 91/12500 [00:01<02:39, 78.04it/s]


  1%|          | 100/12500 [00:01<02:37, 78.57it/s]


  1%|          | 109/12500 [00:01<02:36, 79.17it/s]


  1%|          | 118/12500 [00:01<02:35, 79.54it/s]


  1%|          | 127/12500 [00:01<02:34, 80.01it/s]


  1%|          | 136/12500 [00:01<02:33, 80.29it/s]


  1%|          | 145/12500 [00:01<02:33, 80.69it/s]


  1%|          | 154/12500 [00:01<02:32, 80.92it/s]


  1%|▏         | 163/12500 [00:02<02:

epoch 1 training loss: 1.927





  0%|          | 1/2500 [00:00<04:48,  8.66it/s]


  1%|          | 20/2500 [00:00<00:26, 92.84it/s]


  2%|▏         | 39/2500 [00:00<00:19, 123.41it/s]


  2%|▏         | 60/2500 [00:00<00:16, 143.69it/s]


  3%|▎         | 81/2500 [00:00<00:15, 156.08it/s]


  4%|▍         | 102/2500 [00:00<00:14, 164.08it/s]


  5%|▍         | 123/2500 [00:00<00:13, 169.85it/s]


  6%|▌         | 144/2500 [00:00<00:13, 174.78it/s]


  7%|▋         | 165/2500 [00:00<00:13, 177.91it/s]


  7%|▋         | 186/2500 [00:01<00:12, 180.92it/s]


  8%|▊         | 207/2500 [00:01<00:12, 182.77it/s]


  9%|▉         | 228/2500 [00:01<00:12, 184.65it/s]


 10%|▉         | 249/2500 [00:01<00:12, 185.33it/s]


 11%|█         | 270/2500 [00:01<00:12, 185.22it/s]


 12%|█▏        | 291/2500 [00:01<00:11, 186.47it/s]


 12%|█▏        | 312/2500 [00:01<00:11, 187.61it/s]


 13%|█▎        | 333/2500 [00:01<00:11, 188.66it/s]


 14%|█▍        | 354/2500 [00:01<00:11, 189.85it/s]


 15%|█▌        | 375/2500 [00:01<

...

epoch 5 training loss: 0.897





  0%|          | 1/2500 [00:00<04:52,  8.54it/s]


  1%|          | 20/2500 [00:00<00:26, 91.94it/s]


  2%|▏         | 41/2500 [00:00<00:19, 127.24it/s]


  2%|▏         | 62/2500 [00:00<00:16, 145.49it/s]


  3%|▎         | 82/2500 [00:00<00:15, 155.26it/s]


  4%|▍         | 102/2500 [00:00<00:14, 161.82it/s]


  5%|▍         | 119/2500 [00:00<00:14, 162.59it/s]


  6%|▌         | 140/2500 [00:00<00:14, 167.36it/s]


  6%|▋         | 160/2500 [00:00<00:13, 170.60it/s]


  7%|▋         | 180/2500 [00:01<00:13, 172.94it/s]


  8%|▊         | 200/2500 [00:01<00:13, 174.55it/s]


  9%|▉         | 220/2500 [00:01<00:12, 176.38it/s]


 10%|▉         | 241/2500 [00:01<00:12, 178.34it/s]


 10%|█         | 262/2500 [00:01<00:12, 179.91it/s]


 11%|█▏        | 283/2500 [00:01<00:12, 181.25it/s]


 12%|█▏        | 303/2500 [00:01<00:12, 182.25it/s]


 13%|█▎        | 324/2500 [00:01<00:11, 183.44it/s]


 14%|█▍        | 345/2500 [00:01<00:11, 184.51it/s]


 15%|█▍        | 365/2500 [00:01<

Accuracy of the network on the 10000 test images: 69 %





  0%|          | 1/2500 [00:00<05:23,  7.73it/s]


  1%|          | 17/2500 [00:00<00:33, 74.27it/s]


  1%|▏         | 35/2500 [00:00<00:23, 105.28it/s]


  2%|▏         | 53/2500 [00:00<00:20, 121.37it/s]


  3%|▎         | 70/2500 [00:00<00:18, 130.30it/s]


  3%|▎         | 87/2500 [00:00<00:17, 136.26it/s]


  4%|▍         | 105/2500 [00:00<00:16, 141.35it/s]


  5%|▍         | 122/2500 [00:00<00:16, 144.47it/s]


  6%|▌         | 140/2500 [00:00<00:16, 147.40it/s]


  6%|▋         | 158/2500 [00:01<00:15, 149.76it/s]


  7%|▋         | 176/2500 [00:01<00:15, 151.75it/s]


  8%|▊         | 193/2500 [00:01<00:15, 152.17it/s]


  8%|▊         | 210/2500 [00:01<00:14, 153.24it/s]


  9%|▉         | 227/2500 [00:01<00:14, 154.04it/s]


 10%|▉         | 245/2500 [00:01<00:14, 155.17it/s]


 11%|█         | 263/2500 [00:01<00:14, 156.35it/s]


 11%|█         | 280/2500 [00:01<00:14, 157.05it/s]


 12%|█▏        | 298/2500 [00:01<00:13, 157.75it/s]


 13%|█▎        | 315/2500 [00:01<0

Accuracy of plane : 70 %
Accuracy of   car : 86 %
Accuracy of  bird : 65 %
Accuracy of   cat : 47 %
Accuracy of  deer : 59 %
Accuracy of   dog : 64 %
Accuracy of  frog : 77 %
Accuracy of horse : 66 %
Accuracy of  ship : 79 %
Accuracy of truck : 79 %
Finished Training


In [16]:
print('Epoch 6 to 15')
for epoch in range(5,15):  # loop over the dataset multiple times
    print('epoch ', epoch + 1)
    train(epoch, trainloader, optimizer, criterion)
    test(testloader, net)
    classwise_test(testloader, net)
    torch.save(net.state_dict(), './models/model-'+str(epoch)+'.pth')

print('Finished Training')




  0%|          | 0/12500 [00:00<?, ?it/s]

Epoch 6 to 15
epoch  6





  0%|          | 4/12500 [00:00<05:55, 35.19it/s]


  0%|          | 12/12500 [00:00<03:42, 56.04it/s]


  0%|          | 20/12500 [00:00<03:16, 63.40it/s]


  0%|          | 29/12500 [00:00<03:02, 68.17it/s]


  0%|          | 37/12500 [00:00<02:56, 70.41it/s]


  0%|          | 45/12500 [00:00<02:54, 71.26it/s]


  0%|          | 54/12500 [00:00<02:50, 72.95it/s]


  0%|          | 62/12500 [00:00<02:49, 73.46it/s]


  1%|          | 70/12500 [00:00<02:48, 73.67it/s]


  1%|          | 79/12500 [00:01<02:46, 74.54it/s]


  1%|          | 88/12500 [00:01<02:44, 75.56it/s]


  1%|          | 97/12500 [00:01<02:42, 76.42it/s]


  1%|          | 106/12500 [00:01<02:40, 77.37it/s]


  1%|          | 115/12500 [00:01<02:38, 78.01it/s]


  1%|          | 125/12500 [00:01<02:36, 78.93it/s]


  1%|          | 134/12500 [00:01<02:35, 79.59it/s]


  1%|          | 143/12500 [00:01<02:34, 80.12it/s]


  1%|          | 152/12500 [00:01<02:33, 80.60it/s]


  1%|▏         | 161/12500 [00:01<02:3

epoch 6 training loss: 0.773





  0%|          | 1/2500 [00:00<04:41,  8.87it/s]


  1%|          | 21/2500 [00:00<00:25, 98.69it/s]


  2%|▏         | 42/2500 [00:00<00:18, 134.13it/s]


  3%|▎         | 63/2500 [00:00<00:16, 151.97it/s]


  3%|▎         | 85/2500 [00:00<00:14, 164.62it/s]


  4%|▍         | 107/2500 [00:00<00:13, 172.53it/s]


  5%|▌         | 125/2500 [00:00<00:13, 172.43it/s]


  6%|▌         | 146/2500 [00:00<00:13, 176.85it/s]


  7%|▋         | 166/2500 [00:00<00:13, 179.30it/s]


  7%|▋         | 186/2500 [00:01<00:12, 181.15it/s]


  8%|▊         | 207/2500 [00:01<00:12, 183.69it/s]


  9%|▉         | 228/2500 [00:01<00:12, 185.76it/s]


 10%|▉         | 249/2500 [00:01<00:12, 186.94it/s]


 11%|█         | 270/2500 [00:01<00:11, 188.45it/s]


 12%|█▏        | 291/2500 [00:01<00:11, 189.80it/s]


 12%|█▏        | 312/2500 [00:01<00:11, 190.72it/s]


 13%|█▎        | 333/2500 [00:01<00:11, 191.56it/s]


 14%|█▍        | 354/2500 [00:01<00:11, 192.40it/s]


 15%|█▌        | 375/2500 [00:01<

...

epoch 15 training loss: 0.245





  0%|          | 1/2500 [00:00<04:15,  9.78it/s]


  1%|          | 21/2500 [00:00<00:24, 103.11it/s]


  2%|▏         | 41/2500 [00:00<00:18, 134.58it/s]


  2%|▏         | 62/2500 [00:00<00:16, 151.97it/s]


  3%|▎         | 82/2500 [00:00<00:14, 161.31it/s]


  4%|▍         | 102/2500 [00:00<00:14, 166.91it/s]


  5%|▍         | 123/2500 [00:00<00:13, 172.36it/s]


  6%|▌         | 143/2500 [00:00<00:13, 175.67it/s]


  7%|▋         | 164/2500 [00:00<00:13, 178.54it/s]


  7%|▋         | 185/2500 [00:01<00:12, 181.54it/s]


  8%|▊         | 206/2500 [00:01<00:12, 182.92it/s]


  9%|▉         | 226/2500 [00:01<00:12, 183.08it/s]


 10%|▉         | 246/2500 [00:01<00:12, 184.09it/s]


 11%|█         | 267/2500 [00:01<00:12, 185.75it/s]


 12%|█▏        | 288/2500 [00:01<00:11, 187.18it/s]


 12%|█▏        | 309/2500 [00:01<00:11, 188.28it/s]


 13%|█▎        | 330/2500 [00:01<00:11, 189.34it/s]


 14%|█▍        | 352/2500 [00:01<00:11, 190.51it/s]


 15%|█▍        | 373/2500 [00:01

Accuracy of the network on the 10000 test images: 74 %





  0%|          | 4/2500 [00:00<01:04, 38.85it/s]


  1%|          | 21/2500 [00:00<00:24, 103.04it/s]


  2%|▏         | 38/2500 [00:00<00:19, 124.20it/s]


  2%|▏         | 56/2500 [00:00<00:17, 136.11it/s]


  3%|▎         | 74/2500 [00:00<00:16, 143.71it/s]


  4%|▎         | 92/2500 [00:00<00:16, 148.76it/s]


  4%|▍         | 110/2500 [00:00<00:15, 152.19it/s]


  5%|▌         | 128/2500 [00:00<00:15, 154.09it/s]


  6%|▌         | 144/2500 [00:00<00:15, 154.30it/s]


  6%|▋         | 162/2500 [00:01<00:14, 156.30it/s]


  7%|▋         | 180/2500 [00:01<00:14, 158.02it/s]


  8%|▊         | 198/2500 [00:01<00:14, 159.71it/s]


  9%|▊         | 215/2500 [00:01<00:14, 160.44it/s]


  9%|▉         | 233/2500 [00:01<00:14, 161.64it/s]


 10%|█         | 251/2500 [00:01<00:13, 162.31it/s]


 11%|█         | 269/2500 [00:01<00:13, 162.87it/s]


 11%|█▏        | 287/2500 [00:01<00:13, 163.47it/s]


 12%|█▏        | 305/2500 [00:01<00:13, 164.05it/s]


 13%|█▎        | 323/2500 [00:01<

Accuracy of plane : 77 %
Accuracy of   car : 85 %
Accuracy of  bird : 62 %
Accuracy of   cat : 70 %
Accuracy of  deer : 65 %
Accuracy of   dog : 59 %
Accuracy of  frog : 87 %
Accuracy of horse : 69 %
Accuracy of  ship : 88 %
Accuracy of truck : 83 %
Finished Training
